In [7]:
""" 
json.dumps(): 将 Python 对象编码成 JSON 字符串。 json.dump(): 将 Python 对象编码成 JSON 字符串，并写入到文件中。json.loads(): 将已编码的 JSON 字符串解码为 Python 对象。json.load(): 读取文件中的 JSON 编码的数据，并解码为 Python 对象。
"""
import os
import json
import torch
torch.cuda.is_available()
def json_standard(input_object):
    # print(input_object,type(input_object))
    return json.dumps(input_object,ensure_ascii=False,indent=4)
def read_file(file_path:str):
    with open(file_path,"r",encoding="utf-8") as i_f:
        return json.load(i_f)
def write_file(file_path:str,obj,overwrite=False):
    if os.path.exists(file_path)==False or overwrite==True:
        with open(file_path,"w",encoding="utf-8") as o_f:
            json.dump(obj,o_f,ensure_ascii=False)
        print(f"写入{file_path}")
    else:
        print(f"{file_path}文件已经存在")
def check_file(file_path:str):
    """返回该路径下是否存在文件"""
    is_exist=os.path.exists(file_path)
    if is_exist:
        file_name=file_path.split("/")[-1]
        print(f"{file_name} exist")
    return is_exist

In [8]:
en_data=read_file("/home/ckqsudo/code2024/EMNLP2024/Final_Cache/en_data_emo_stra_labels__6_9.json")
cn_data=read_file("/home/ckqsudo/code2024/EMNLP2024/Final_Cache/cn_data_emo_stra_labels__6_11.json")

In [9]:
# en_data[0]["topic_dialog"]["dialog"]
sum([len(item["topic_dialog"]["dialog"]) for item in en_data ])

6208

In [10]:
# en_data[4]['topic_dialog']['dialog'][3]
strategies=[
    {"label": "Question", "example": "Can you talk more about your feelings at that time?"},
    {"label": "Restatement or Paraphrasing", "example": "It sounds that you feel like everyone is ignoring you. Is it correct?"},
    {"label": "Reflection of Feelings", "example": "I understand how anxious you are."},
    {"label": "Self-disclosure", "example": "I feel the same way! I also don't know what to say to strangers."},
    {"label": "Affirmation and Reassurance", "example": "You've done your best and I believe you will get it!"},
    {"label": "Providing Suggestions", "example": "Deep breaths can help people calm down. Could you try to take a few deep breaths?"},
    {"label": "Information", "example": "Apparently, lots of research has found that getting enough sleep before an exam can help students perform better."},
    {"label": "Others", "example": "Yeah, I am glad to help you."}
    ]

In [11]:
label_list=["Question", "Restatement or Paraphrasing", "Reflection of Feelings", "Self-disclosure", "Affirmation and Reassurance", "Providing Suggestions", "Information", "Others","Role-play", "Unknown"]

In [1]:
from openai import OpenAI
import os
import time
import copy
import json
client = OpenAI()
client.base_url='https://gptnb.keqichen.top/v1'
result=[]
def get_strategy_messages(dialog_history:list):

  # emo_label_few_shot_str=json.dumps(emo_label_few_shot)

  example_list=[{"role":"user","content":"[...{'role':'Therapist','content':'One of your underlying assumptions is ‘If I don’t have a real job then I’m not as good as others’. Now you’ve been out of work for several years due to illness and you said you try to cram a lot of activity into each day to prove that you are as good as others by having a job at home, so to speak; so do you see reading the newspaper or watching television as an indulgence, idling when you should be striving?'}]"},{"role":"assistant","content":"{'strategy':[\'Reflection of Feelings\', \'Self-disclosure\',\'Question\']}"}]
  for idx,item in enumerate(strategies):
    example_list.append({"role":"user","content":"[...{'role':'Therapist','content':'"+item['example']+"'}]"})
    return_str_json={"strategy":f"['{item['label']}']"}
    example_list.append({"role":"assistant","content":json.dumps(return_str_json)})
  messages=[
    {"role": "system", "content": f" Please classify the strategy of the last utterance from the therapist. There are some examples:"},
  ]
  messages.extend(example_list)
  gpt_history=[]
  for dialog_item in dialog_history:
    if 'Therapist' in dialog_item['participant']:
      gpt_history.append({"role": "Therapist", "content":dialog_item['text']})
    else:
      gpt_history.append({"role": "Client", "content":dialog_item['text']})
  messages.extend([
    {"role": "user","content": f"""Yes, there is the dialog history. {str(gpt_history)}. Please classify the strategy of the last utterance from the therapist and respond with a list of labels in JSON format. The possible strategies must be within these labels: {str(label_list)}"""}
    ]
  )
  return messages
  

def get_price(total_token:int):
  return f"GPT-4:{total_token/1000000*10}$ GPT-3:{total_token/1000000*0.5}$"

def get_stragegy_label(cur_data,cur_type="en",cur_day="6_11"):
  therapist_keyword='Therapist' if cur_type=="en" else "治疗师"
  counter=0
  token_sum=0
  for x,topic in enumerate(cur_data):
    dialog_list=cur_data[x]['topic_dialog']['dialog']
    for y in range(0,len(dialog_list)):
      dialog_history=copy.deepcopy(dialog_list[max(y-4,0):y]+[dialog_list[y]])
      if therapist_keyword in dialog_history[-1]['participant']:
        counter+=1
        gpt_3_5_model="gpt-3.5-turbo"
        emo_messages=get_strategy_messages(dialog_history)
        top_p=0.3
        for _ in range(2):
          completion = client.chat.completions.create(
            model=gpt_3_5_model,
            messages=emo_messages,
            top_p=top_p
          )
          token_sum+=completion.usage.total_tokens
          choice=completion.choices[0]
          reponse_res=str(choice.message.content)
          label_res=[label for label in label_list if label in reponse_res]
          if len(label_res)>0:
            break
          else:
            top_p-=0.05
            print("##",reponse_res)
        if len(label_res)==0:
          label_res.append("Others")
        time.sleep(0.001)
        print(x,counter,token_sum,get_price(token_sum),label_res,len(label_res))
        print(x,counter,token_sum,choice.message.content)
        cur_data[x]['topic_dialog']['dialog'][y]['strategy']=label_res
        write_file(f"/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/{cur_type}_{cur_day}_data_stra_labels—j.json",cur_data,True)
    print(token_sum,"\n\n\n\n")
  return cur_data
# get_stragegy_label(en_data,cur_type="en",cur_day="6_11")

In [476]:

emo_dict=[
{"label": "Anxiety", "example": "Yes, I am. When I don't have to relate everything to childhood sexual conflicts, I can listen better. / I’m walking down the high street. I feel very uncomfortable. I think everyone is looking at me, so I keep my head down. / I see them staring at me, judging me. I hate it."},
{"label": "Depression", "example": "But I didn't stay angry long at Nancy when she left me. I got depressed."},
{"label": "Sadness", "example": "I’m walking down the high street. I feel very uncomfortable. I think everyone is looking at me, so I keep my head down."},
{"label": "Anger", "example": "I never told you about my grandmother, did I?"},
{"label": "Fear", "example": "I'd say the only difference is that this time you'd be in the role of apprentice rather than teacher, and that more than sex per se is what frightens you..."},
{"label": "Guilty", "example": "I didn’t bring her up right. It’s my fault that she behaves as she does. If I’d been a good mother she wouldn’t have turned out like this. I’m a bad mother."},
{"label": "Shame", "example": "And the family I live with doesn’t know that."},
{"label": "Neutral", "example": "It doesn't really matter to me either way."},
{"label": "Unknown", "example": "Right."},
{"label": "Others", "example": "#Those utterances that don't belong to the classification above.#"},
{"label":'Happiness',"example":"I’m beginning to move about a bit and am beginning to nod my head and attempt to smile as if I’m in on the joke."}
]
emo_labels=['Anxiety',
 'Depression',
 'Sadness',
 'Anger',
 'Fear',
 'Guilty',
 'Shame',
 'Neutral',
 'Unknown',
 'Others',
 'Happiness']

In [473]:
en_data=read_file("/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/en_data_emo_stra_labels_6_12_final.json")

In [487]:
from openai import OpenAI
import os
import time
import copy
import json
client = OpenAI()
client.base_url='https://gptnb.keqichen.top/v1'
result=[]
def get_emotional_labels_messages(dialog_history:list):

  # emo_label_few_shot_str=json.dumps(emo_label_few_shot)
  example_list=[]
  for idx,item in enumerate(emo_dict):
    example_list.append({"role":"user","content":"[...{'role':'Client','content':'"+item['example']+"'}]"})
    return_str_json={"emotional label":f"['{item['label']}']"}
    example_list.append({"role":"assistant","content":json.dumps(return_str_json)})
  messages=[
    {"role": "system", "content": f" Please classify the emotional label of the last utterance from the therapist. There are some examples:"},
  ]
  messages.extend(example_list)
  gpt_history=[]
  for dialog_item in dialog_history:
    if 'Therapist' in dialog_item['participant']:
      gpt_history.append({"role": "Therapist", "content":dialog_item['text']})
    else:
      # gpt_history.append({"role": "Client", "content":dialog_item['text'],"observation":dialog_item['observation']})
      gpt_history.append({"role": "Client", "content":dialog_item['text']})
  messages.extend([
    {"role": "user","content": f"""Yes, there is the dialog history. {str(gpt_history)}. Please classify the emotional label of the last utterance from the Client with reference to the conversation history. Please respond with a list of labels in JSON format, and the possible emotional labels must be within these labels: {str(emo_labels)}"""}
    ]
  )
  return messages
def get_emo_label(cur_data,cur_type="en",cur_day="6_11"):
  counter=0
  token_sum=0
  therapist_word='Therapist' if cur_type=="en" else "治疗师" 
  for x,topic in enumerate(cur_data):
    dialog_list=cur_data[x]['topic_dialog']['dialog']
    for y in range(0,len(dialog_list)):
      dialog_history=copy.deepcopy(dialog_list[max(y-4,0):y]+[dialog_list[y]])
      if 'emotional label' in dialog_history[-1] and type(dialog_history[-1]['emotional label'])==list:
        print("跳过",dialog_history[-1]['emotional label'])
        continue
      if therapist_word not in dialog_history[-1]['participant']:
        counter+=1
        gpt_3_5_model="gpt-3.5-turbo"
        messages=get_emotional_labels_messages(dialog_history)
        top_p=0.3
        for _ in range(2):
          completion = client.chat.completions.create(
            model=gpt_3_5_model,
            messages=messages,
            top_p=top_p
          )
          token_sum+=completion.usage.total_tokens
          choice=completion.choices[0]
          reponse_res=str(choice.message.content)
          label_res=[label for label in emo_labels if label in reponse_res]
          if len(label_res)>0:
            break
          else:
            top_p-=0.05
            print("##",reponse_res)
        if len(label_res)==0:
          label_res.append("Unknown")
          print("###",reponse_res)
        time.sleep(0.01)
        print(x,counter,token_sum,get_price(token_sum),label_res,len(label_res))
        print(x,counter,token_sum,choice.message.content,dialog_history[-1]['text'])
        cur_data[x]['topic_dialog']['dialog'][y]['emotional label']=label_res
        write_file(f"/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/{cur_type}_data_emo_stra_labels_{cur_day}_final_j.json",cur_data,True)
    print(token_sum,"\n\n\n\n")
# get_emo_label(en_data,cur_type="en",cur_day="6_12")

In [482]:
get_stragegy_label(cn_data,cur_type="cn",cur_day="6_12")  
# get_emo_label(cn_data,cur_type="cn",cur_day="6_12")

0 1 663 GPT-4:0.00663$ GPT-3:0.0003315$ ['Unknown'] 1
0 1 663 {"strategy": "['Unknown']"}
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/cn_6_12_data_stra_labels.json
0 2 1410 GPT-4:0.0141$ GPT-3:0.000705$ ['Question'] 1
0 2 1410 {"strategy": ["Question"]}
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/cn_6_12_data_stra_labels.json
0 3 2386 GPT-4:0.02386$ GPT-3:0.001193$ ['Role-play'] 1
0 3 2386 {"strategy": ["Role-play"]}
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/cn_6_12_data_stra_labels.json
2386 




1 4 3120 GPT-4:0.0312$ GPT-3:0.00156$ ['Restatement or Paraphrasing'] 1
1 4 3120 {"strategy": ["Restatement or Paraphrasing"]}
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/cn_6_12_data_stra_labels.json
1 5 4099 GPT-4:0.04099$ GPT-3:0.0020495$ ['Providing Suggestions'] 1
1 5 4099 {
    "strategy": ["Providing Suggestions"]
}
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/cn_6_12_data_stra_labels.json
1 6 5116 GPT-4:0.05116$ GPT-3:0.002558$ ['Question'] 1
1

[{'theme': '',
  'chat_stage': 'Early Session',
  'is_same_qa': '',
  'is_same_case': 0,
  'background': '来访者是一个正在接受多模式行为主义治疗的个体，面临着焦虑、情感问题和自我认知方面的挑战。她可能正在寻求改变负面行为模式、缓解紧张和疾患、增强自我控制的帮助。',
  'pre_reasoning': '行为主义治疗\n行为主义治疗概述\n为主治疗法御法的核心目标在于消除来访者适应不良的行为方式，代之以更有建设性的行为方式。也就是说要找出导致来访者行为问题的思维方式，教以新的思维方式，从而改变他们原来的行为方式。\n常见的行为主义治疗技术有：系统离散法、实景暴露法、释恩谈练、强化、示范、社交技能练习、自我管理项目练习，专注于接纳技术、行为排练、指导以及其他多种方式的技术。评估和诊断在确定治疗计划的阶段进行。其中，治疗师会采用“什么”、“怎样”以及“何时”这样的问题（但不会使用“为什么”这样的问题）。\n这种方法有其独特的优势：可以确立明确的、易于管理的和可测量的行为目标并可以将此作为治疗的焦点。在治疗开始时，个体的行为将被测量，从而得到一个基准水平。\n因此，在后来的治疗过程中，治疗师就可以在给定的维度上将来访者的行为与其基准水平进行比较而得出治疗的进度。这外，评估和治疗是同时进行的，来访者将频繁地面对治疗师提出的这个问题：“我们现在做的事情是否可以帮助你达到你所预期的改变呢？”这样，来访者可以很容易确定什么时候应该停止治疗。\n多模式行为主义治疗专家阿诺·A·拉扎尔斯博士对来访者的分析\n引言\n多模式治疗是一种系统的行为主义治疗，强调技术上的折衷主义，即根据来访者的特定问题选择不同的治疗手段。治疗师根据BASICI.D.领域（行为、情绪、感知觉、意识、认知、人际关系、药物和生物因素）进行多模式评估，以确保具体问题。在行为层面，治疗师关注来访者的焦虑、避免眼神接触、睡眠不足等行为。在情感层面，治疗师关注沮丧、忧郁、惊恐等情感问题。在认知、感知、意识、人际关系和药物生物因素层面，治疗师也分别关注来访者的具体问题。治疗师通过多模式评估全面了解来访者的问题，为制定个性化的治疗计划提供了重要依据。和杰拉德·治疗师一样，我首先不会考虑采用诊断术语来对来访者进行定位。实

In [488]:
get_emo_label(cn_data,cur_type="cn",cur_day="6_12")

0 1 781 GPT-4:0.00781$ GPT-3:0.0003905$ ['Neutral'] 1
0 1 781 {"emotional label": "['Neutral']"} 是的，我想我可以。
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/cn_data_emo_stra_labels_6_12_final_j.json
0 2 1654 GPT-4:0.01654$ GPT-3:0.000827$ ['Neutral'] 1
0 2 1654 {"emotional label": "['Neutral']"} 我希望看到十岁时的自己。
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/cn_data_emo_stra_labels_6_12_final_j.json
跳过 ['Anger']
1654 




1 3 2509 GPT-4:0.02509$ GPT-3:0.0012545$ ['Depression'] 1
1 3 2509 {"emotional label": "['Depression']"} 也许我应该再减一次肥。
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/cn_data_emo_stra_labels_6_12_final_j.json
1 4 3597 GPT-4:0.03597$ GPT-3:0.0017985$ ['Neutral'] 1
1 4 3597 {"emotional label": "['Neutral']"} 当然。
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck/cn_data_emo_stra_labels_6_12_final_j.json
1 5 4615 GPT-4:0.046150000000000004$ GPT-3:0.0023075$ ['Neutral'] 1
1 5 4615 {"emotional label": "['Neutral']"} 关于什么？
写入/home/ckqsudo/code2024/EMNLP2024/Final_Cach

In [ ]:
# write_file("/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck_6_12/en_data.json",en_data,True)
write_file("/home/ckqsudo/code2024/EMNLP2024/Final_Cache/fuck_6_12/cn_data.json",cn_data,True)
